In [87]:

# This program is meant to help build features 
import pandas as pd
import numpy as np
import math
import matplotlib.pyplot as plt
from scipy.interpolate import spline
from path import Path
from os import listdir
import os
from os.path import isfile, join
import shutil
from scipy import signal
import sys
from tsfresh import extract_features
from tsfresh import select_features
from tsfresh.utilities.dataframe_functions import impute
from tsfresh import extract_relevant_features
from tsfresh.feature_extraction import extract_features, EfficientFCParameters


noise = -92

class Peak:
    def __init__(self, start, end, height):
        self.start = start
        self.end = end
        self.width = end - start
        self.height = height
    def getStart(self):
        return self.start
    def getEnd(self):
        return self.end
    def getWidth(self):
        return self.width
    def getHeight(self):
        return self.height               
    def __str__(self):
        return "START: " + str(self.start) + "; END: " + str(self.end) + "; WIDTH: " + str(self.width) + "; HEIGHT: " + str(self.height)
    def __repr__(self):
        return str(self) + '\n'



       
def whiskerStDev(df, peak):
     # this method is meant to find the standard deviation of between 
    # the top and bottom end of the whisker. To achieve this, I will 
    # find the center of the peak, and look for the max and min of the 
    # center left and center right of the whisker
    # samples around the center
    
    start = peak.getStart()
    end = peak.getEnd()
    
    center = (start + end) // 2
    
    centerLeft = (center + start)//2
    centerRight = (center + end)//2
    
    stdev = df['Amplitude'].loc[centerLeft : centerRight].std()
    
    if math.isnan(stdev):
        raise SystemExit
        return 0
    return stdev
    
    
    

    
def whiskerHeight(df, peak):
    # this method is meant to find the difference between the top 
    # and bottom end of the whisker. To achieve this, I will find 
    # the center of the peak, and look for the max and min of the 
    # center left and center right of the whisker
    # samples around the center

    start = peak.getStart()
    end = peak.getEnd()
    
    center = (start + end) // 2
    
    centerLeft = (center + start)//2
    centerRight = (center + end)//2
    
    maximum = df['Amplitude'].loc[centerLeft : centerRight].max()
    minimum = df['Amplitude'].loc[centerLeft : centerRight].min()

    if math.isnan(maximum) or math.isnan(minimum):
        raise SystemExit
        return 0
    return maximum - minimum

    
def getDeviceName(subdir):
    i = -1
    device = ''
    while abs(i) < len(subdir):
        if not subdir[i] == '\\':
            device += subdir[i]
            i -= 1
        else:
            return device[::-1]
        
def deviceArr(path):
    
    devices = []
    
    my_directory = Path(path)
    subdirs = my_directory.dirs()
    
    i = 0
    for subdir in subdirs:
        devices.insert(i, getDeviceName(subdir))
        i+=1
    return devices

def makeDir(pathWay):
    if os.path.isdir(pathWay):
        shutil.rmtree(pathWay)
        
    os.mkdir(pathWay)
    
def getBurstNum(file):
    i = -1
    num = ''
    
    while abs(i) < len(file):
        if not file[i] == '(':
            i -= 1
            
        else:
            i-=1
            while abs(i) < len(file) and file[i] != 't': 
                num += file[i]
                i-=1
                    
            return int(num[::-1])
        
        
def ts(timeseries):
    
    y = timeseries["Device"]
    y = y.reindex(index = timeseries.index)
    extracted_features = extract_features(timeseries, column_id="Device", column_sort="Time", 
                                          default_fc_parameters=EfficientFCParameters())
    impute(extracted_features)
#     features_filtered = select_features(extracted_features, y)
#     print(extracted_features)
    extracted_features.to_excel("timeseriesFeatures.xlsx")

#     features_filtered_direct = extract_relevant_features(timeseries, y,
#                                                      column_id='Device', column_sort='Time')
#     features_filtered.to_excel("relevantFeatures.xlsx")
    return extracted_features
    
    
    
    
if __name__ == "__main__":
    # assumptions, there is a directory which has folders labelled by device name. The folder contains amplitude information. 
    # requirements: must be able to pick up the two strongest plateaus
    # will use python peak detection to find out the two or one peaks worth looking at. Will look at the most prominent peaks
    # first.
    path = r'newBursts'
    savePlotsTo = r'Plots'
    featuresFolder = r'Features'
    samplingRate = 112*(10**6) # sampling rate of collection device in samples/second
    minLength = 40/(10**6) # min length of a bluetooth packet (8us for preamble and 32us for access address) in seconds
    minWidth = minLength * samplingRate #minwidth is 4480samples
    
    features = pd.DataFrame(columns = ['Bursts', 'Device', 'Burst Width','Burst-Top Height',
                                                          'Burst-Top Stdev'])
    mainseries = pd.DataFrame()
    devices = deviceArr(path)
    
    my_directory = Path(path)
    subdirs = my_directory.dirs()
    
    makeDir(savePlotsTo)
    makeDir(featuresFolder)
    
    mainseries = pd.DataFrame()
    for device in devices:
        makeDir(savePlotsTo + '//' + device) #make folder to save plots to
        
        print(device)
        subdir = path + '\\' + device
        
        bursts = [f for f in listdir(subdir) if isfile(join(subdir, f))]
        
        size = len(bursts) * 2 # we expect each burst to contain 2 bursts
        
        df = pd.DataFrame(index = range(size), columns = ['Bursts', 'Device', 'Burst Width','Burst-Top Height',
                                                          'Burst-Top Stdev'])
        i = 0
        
        for file in bursts:
            
            fileDir = path + '\\' + device + '\\' + file
            print(fileDir)
            data = pd.read_excel(fileDir)
            
            peak = Peak(data['Time'].iloc[0], data['Time'].iloc[-1], data['Amplitude'].mean())
            print(peak)
            burstNum = getBurstNum(file)
            df['Bursts'][i] = burstNum
            df['Device'][i] = device
            df['Burst Width'][i] = peak.getWidth()
            df['Burst-Top Height'][i] = whiskerHeight(data, peak)
            df['Burst-Top Stdev'][i] = whiskerStDev(data, peak)
            
            data = data.reset_index(drop = True) # Has to be here to avoid messing up peak above
            
            timeseries = ts(data)
                
            tsFeatures = list(timeseries)

            for feat in tsFeatures:
                if feat not in df.columns:
                    df[feat] = 'NaaaaN'
                df[feat][i] = timeseries[feat][0]

            mainseries = mainseries.append(data)
            i+=1
                
            
                
#         print(df)
        df = df.reindex(range(i))
        df.to_excel(featuresFolder + "\\" + device + '.xlsx')
        features = features.append(df)
    
features = features.reset_index(drop = True)
print(features)

features.to_excel(featuresFolder + '\\Features.xlsx')
            
            #smooth the data



Apple watch
newBursts\Apple watch\Burst000(a).xlsx
START: 164233; END: 173907; WIDTH: 9674; HEIGHT: -64.94329470618459





Feature Extraction:   0%|                                                                        | 0/1 [00:00<?, ?it/s]


Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 1/1 [00:04<00:00,  4.76s/it]

newBursts\Apple watch\Burst000(b).xlsx
START: 192293; END: 201860; WIDTH: 9567; HEIGHT: -65.4697873900904





Feature Extraction:   0%|                                                                        | 0/1 [00:00<?, ?it/s]


Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 1/1 [00:04<00:00,  4.68s/it]

newBursts\Apple watch\Burst001(a).xlsx
START: 162592; END: 174381; WIDTH: 11789; HEIGHT: -70.67487431969104


...




Feature Extraction:   0%|                                                                        | 0/1 [00:00<?, ?it/s]


Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 1/1 [00:09<00:00,  9.56s/it]

newBursts\Pyle Health 2\Burst078(b).xlsx
START: 70551; END: 91147; WIDTH: 20596; HEIGHT: -64.79027219979713





Feature Extraction:   0%|                                                                        | 0/1 [00:00<?, ?it/s]


Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 1/1 [00:09<00:00,  9.72s/it]C:\Users\f0031pt\AppData\Local\Continuum\miniconda3\envs\ml\lib\site-packages\pandas\core\frame.py:6211: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


     Amplitude__abs_energy Amplitude__absolute_sum_of_changes  \
0              4.10696e+07                            5356.78   
1              4.12001e+07                            5305.65   
2                6.027e+07                            18794.9   
3               8.4602e+07                              35830   
4              5.94503e+07                            18035.9   
5              5.37268e+07                            14303.9   
6              5.36013e+07                            14025.1   
7              6.70926e+07                            23197.1   
8              5.59376e+07                            15126.5   
9              5.72188e+07                            16168.4   
10             5.03249e+07                            11504.5   
11             5.86238e+07                            16728.9   
12             9.72901e+07                            38911.7   
13             6.97267e+07                            12470.1   
14             9.79819e+0

[7312 rows x 793 columns]
